In [1]:
import os
import sys
import re
import numpy as np
import pickle
from scipy.optimize import fmin
import multiprocessing as mp
import functools

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
# statmech library setup
sys.path.append('../../statmechlib')
from statmechlib.preprocessing import select_nodes, to_param_dict, to_param_list, insert_zero_params, rescale_manybody_params
from statmechlib.preprocessing import Trajectory, scale_configuration, pair_dist_cutoff, find_index
from statmechlib.forcefields import sd2_loss, utot_EAM_per_atom, utot_EAM_per_box, ftot_EAM, udif_print, u_core
from statmechlib.preprocessing import universal_eos
from statmechlib.preprocessing import pair_dist, force_targ, get_stats_EAM_per_atom, get_stats_EAM_per_box

In [4]:
target_raw = '../data/target_raw'
target_proc = '../data/target_processed'
working = '../data/working'

In [5]:
# stats_file = 'stats_marinica' # 'stats_samples'
# target_file = 'target_marinica' # 'target_samples'
params_file = 'marinica_params'
# stats_file = 'stats_manyknots' # 'stats_samples'
# target_file = 'target_manyknots' # 'target_samples'
# stats_file = 'stats_manymd' # 'stats_samples'
# target_file = 'target_manymd' # 'target_samples'
stats_file = 'stats_manyall' # 'stats_samples'
target_file = 'target_manyall' # 'target_samples'
# stats_file = 'stats_everything' # 'stats_samples'
# target_file = 'target_everything' # 'target_samples'
stats_md_file = 'stats_onlymd' # 'stats_samples'
target_md_file = 'target_onlymd' # 'stats_samples'

In [6]:
with open(os.path.join(working, stats_file+'.pickle'), 'rb') as fi:
    stats_all = pickle.load(fi)

with open(os.path.join(working, target_file+'.pickle'), 'rb') as fi:
    targets = pickle.load(fi)
    
with open(os.path.join(working, stats_md_file+'.pickle'), 'rb') as fi:
    stats_md = pickle.load(fi)
    
with open(os.path.join(working, target_md_file+'.pickle'), 'rb') as fi:
    targets_md = pickle.load(fi)

with open(os.path.join(working, params_file + '.pickle'), 'rb') as fi:
    param_list = pickle.load(fi)  

In [7]:
def downselect(stats_inp, pair_knots, edens_knots):
    
    # find idices of knots
    pair_index = find_index(pair_knots, stats_inp['hyperparams']['pair'])
    edens_index = find_index(edens_knots, stats_inp['hyperparams']['edens'])
    
    # create boolean arrays with select indices set to True
    p_ix = np.array([True if i in pair_index else False for i in range(len(stats_inp['hyperparams']['pair']))])
    m_ix = np.array([True if i in edens_index else False for i in range(len(stats_inp['hyperparams']['edens']))])

    stats_out = select_nodes(stats_inp, p_ix, m_ix)
    
    return stats_out

In [8]:
pair_knots = [2.22, 2.46, 2.5648975,  2.629795 ,  2.6946925,  2.8663175,  2.973045 ,
        3.0797725,  3.5164725,  3.846445 ,  4.1764175,  4.700845 ,
        4.8953   ,  5.089755 ,  5.3429525,  5.401695 ,  5.4604375]
edens_knots = [ 2.22, 2.5,  2.6946925, 2.8663175, 3.1,  3.5,  4.5]

In [9]:
stats = downselect(stats_all, pair_knots, edens_knots)
print(stats['hyperparams'])
stats_select_md = downselect(stats_md, pair_knots, edens_knots)
print(stats_select_md['hyperparams'])

{u'pair': [2.2200000000000002, 2.46, 2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003], u'edens': [2.2200000000000002, 2.5, 2.6946924999999999, 2.8663175000000001, 3.1000000000000001, 3.5, 4.5]}
{u'pair': [2.2200000000000002, 2.46, 2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003], u'edens': [2.2200000000000002, 2.5, 2.6946924999999999, 2.8663175000000001, 3.1000000000000001, 3.5, 4.5]}


In [10]:
targets['md'] = targets_md['md']
stats['md'] = stats_select_md['md']

In [11]:
for key in sorted(targets.keys()):
    for box, xyz, ene in zip(targets[key]['box'], targets[key]['xyz'], stats[key]['energy']):
        n = len(xyz)
        vol = np.linalg.det(box)
        corr = float(n*n)/vol
        ene.append([corr])

In [12]:
stats['bcc_npt_langevin_300K']['energy'][0][:]

[array([  0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          4.32452672e-04,   2.40108437e-01,   1.49699018e+01,
          3.67830273e+01,   6.58053659e+01,   2.44033647e+02,
          4.40325883e+02,   6.80111008e+02,   1.13544979e+03,
          1.32771865e+03,   1.53444986e+03,   1.82571708e+03,
          1.89696652e+03,   1.96972937e+03]),
 array([  0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          4.37184093e-15,   3.18476767e-07,   2.82775234e-02,
          9.17736776e-01,   9.14748666e+00,   1.69749763e+03,
          1.79543454e+04,   1.02110145e+05,   7.92918644e+05,
          1.48233268e+06,   2.64426772e+06,   5.29910283e+06,
          6.17592659e+06,   7.17934901e+06]),
 array([  0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          9.35076567e-08,   2.01440000e-03,   1.80322649e+00,
          1.06606591e+01,   3.39604107e+01,   4.65546847e+02,
          1.51515052e+03,   3.61420678e+03,   1.00729590e+04,
          1.37729635e+04,   1.83956954e+

In [13]:
targets['eos_fcc']['weight'] = 0.0
targets['bain']['weight'] = 0.0
targets['eos']['weight'] = 0.0
targets['eos_bcc']['weight'] = 0.0
targets['relax']['weight'] = 0.0
#targets['liq_5000K']['weight'] = 0.1

In [14]:
targets.keys()

['bcc_npt_langevin_3700K',
 'md',
 'vac_npt_langevin_2000K',
 'relax',
 'screw_111_npt_langevin_2000K',
 'bcc_npt_langevin_300K',
 'i111_npt_langevin_2000K',
 'eos',
 'fcc_npt_langevin_300K',
 'eos_fcc',
 'i110_npt_langevin_2000K',
 'liq_3700K',
 'liq_5000K',
 'eos_bcc',
 'bain']

In [15]:
[(key, targets[key]['weight']) for key in targets.keys()]

[('bcc_npt_langevin_3700K', 1.0),
 ('md', 1.0),
 ('vac_npt_langevin_2000K', 1.0),
 ('relax', 0.0),
 ('screw_111_npt_langevin_2000K', 1.0),
 ('bcc_npt_langevin_300K', 1.0),
 ('i111_npt_langevin_2000K', 1.0),
 ('eos', 0.0),
 ('fcc_npt_langevin_300K', 1.0),
 ('eos_fcc', 0.0),
 ('i110_npt_langevin_2000K', 1.0),
 ('liq_3700K', 1.0),
 ('liq_5000K', 1.0),
 ('eos_bcc', 0.0),
 ('bain', 0.0)]

In [17]:
start_params = []
# start_params.append([ -4.18353755e+00,  -9.63668936e-03,  0.0, -1.00171035e+02,
#          1.90025394e+01,   2.15938317e+01,  -1.39759833e+01,
#          2.16332289e+01,  -3.29542126e+00,   1.70455674e+00,
#          1.41347064e+00,  -9.02958785e-01,  -8.62309098e-01,
#          1.95964588e+00,  -8.70527088e-01,   3.22342700e-02,
#         -1.53866121e+00,   1.37095441e+00,  -4.32896107e+01,
#          4.64461212e+00,   3.23329113e-01,   5.82061842e-02, -0.1])
# start_params.append([ -4.36548916e+00,  -1.11867827e-02,  -1.94093020e+01,
#         -1.40195282e+02,   4.53864231e+01,   1.49756180e+01,
#         -1.36031385e+01,   2.21581200e+01,  -4.61501041e+00,
#          2.06360250e+00,   1.12795645e+00,  -8.01200744e-01,
#         -8.58426028e-01,   1.95860157e+00,  -8.68817546e-01,
#          2.43936831e-02,  -1.54555297e+00,   1.38005891e+00,
#         -5.22754243e+01,   3.98209114e+00,   3.07369702e-01,
#          5.51658454e-02,   1.58601447e+00])
# start_params.append([ -4.16739003e+00,  -4.97036785e-03,  -4.62426912e+02,
#          2.63469650e+02,   1.00253629e+01,   2.05151925e+01,
#         -1.36702712e+01,   2.29129977e+01,  -1.27210473e+01,
#          2.95533783e+00,   8.18470873e-01,  -7.89494754e-01,
#         -8.74455389e-01,   2.10177842e+00,  -9.22682795e-01,
#         -6.93852493e-02,  -1.52166575e+00,   1.40766925e+00,
#          1.52571934e+02,   3.37536873e-01,   6.89310740e-01,
#          4.87102227e-02,   2.79573955e+00])
# start_params.append([ -4.33954858e+00,  -1.02215197e-02,  0.0, -1.12590032e+02,
#          3.06702045e+01,   1.74951979e+01,  -1.33298120e+01,
#          2.13899957e+01,  -3.70881631e+00,   1.56452640e+00,
#          1.27789071e+00,  -8.54623702e-01,  -8.39818015e-01,
#          1.95990543e+00,  -8.75948596e-01,   1.81927625e-02,
#         -1.54683863e+00,   1.38614460e+00,  -4.28747460e+01,
#          4.18974818e+00,   1.56622590e-01,   5.72961538e-02,
#          3.46319317e+00])

# start_params.append([ -4.41712815e+00,  -7.57807965e-03, 0.0, 2.79276814e+02,
#          1.74479561e+02,  -6.59620942e+01,   3.53977481e+01,
#         -1.40546374e+01,   2.11913467e+01,  -4.95603366e+00,
#          8.26392820e-01,   1.26391280e+00,  -9.48799563e-01,
#         -7.79099318e-01,   2.00268261e+00,  -8.90495881e-01,
#         -8.59210993e-03,  -1.54948191e+00,   1.39577855e+00,
#          2.43904610e+02,   3.47694754e+00,  -3.14999583e-01,
#          6.33069119e-02,   5.60287637e+00])

# start_params.append([-4.48347382e+00,  -7.78079006e-03,   2.92055760e+02,
#          1.84809430e+02,  -6.18705307e+01,   3.27735461e+01,
#         -1.36588262e+01,   2.11547368e+01,  -5.45394162e+00,
#          8.02998352e-01,   1.21949599e+00,  -9.43034331e-01,
#         -7.71285316e-01,   2.00564540e+00,  -8.93039729e-01,
#         -9.92574423e-03,  -1.55106037e+00,   1.39898785e+00,
#          2.54912062e+02,   3.19484582e+00,  -3.49947883e-01,
#          6.32970386e-02,   4.13612869e+00])

# start_params.append([ -4.41712815e+00,  -7.57807965e-03, 0.0, 2.79276814e+02,
#          1.74479561e+02,  -6.59620942e+01,   3.53977481e+01,
#         -1.40546374e+01,   2.11913467e+01,  -4.95603366e+00,
#          8.26392820e-01,   1.26391280e+00,  -9.48799563e-01,
#         -7.79099318e-01,   2.00268261e+00,  -8.90495881e-01,
#         -8.59210993e-03,  -1.54948191e+00,   1.39577855e+00,
#          2.43904610e+02,   3.47694754e+00,  -3.14999583e-01,
#          6.33069119e-02])

# start_params.append([ -3.09187534e+00,   1.19622206e-04,  -5.67875917e+02,
#          3.21802084e+02,  -4.71317094e+02,   3.98296604e+02,
#         -1.13270858e+02,   6.03114401e+00,   1.48067908e+01,
#         -1.57531660e+01,   7.80863462e+00,  -2.99246651e+00,
#          7.33596451e-01,  -9.50794219e-01,   1.94186078e+00,
#         -8.83596676e-01,  -1.33608784e-01,  -1.46694544e+00,
#          1.42447434e+00,   7.53865380e+01,   3.29733034e-01,
#          2.18327852e+00,   6.63152141e-02, 0.0])

# start_params.append([ -2.95016477e+00,   3.78177969e-04,  -5.21095611e+02,
#          3.09845244e+02,  -4.69222440e+02,   3.95186037e+02,
#         -1.11630659e+02,   5.36915127e+00,   1.52984702e+01,
#         -1.54915170e+01,   7.53107481e+00,  -2.98591742e+00,
#          7.55346307e-01,  -1.00678488e+00,   1.96634582e+00,
#         -8.71560927e-01,  -1.41820832e-01,  -1.46508000e+00,
#          1.42936365e+00,   7.23805795e+01,   0.0, 9.18071460e-01,
#          2.04259992e+00,   6.28575567e-02,   7.62804667e-03])

# start_params.append([ -3.27882058e+00,  -9.77681860e-04,  -5.95486537e+02,
#          3.42401535e+02,  -4.15497479e+02,   3.71316746e+02,
#         -1.07274610e+02,  -2.93282898e+00,   1.51298572e+01,
#         -1.37454674e+01,   8.16724633e+00,  -3.16850352e+00,
#          8.74607042e-01,  -1.07878768e+00,   1.97939820e+00,
#         -8.26149646e-01,  -1.62437297e-01,  -1.45694910e+00,
#          1.42153527e+00,   1.29203135e+02,  -9.25284676e+00,
#          2.63967417e+00,   2.06410900e+00,   6.03258240e-02*2])

# start_params.append([ -3.56709315e+00,  -2.97358686e-03,  -4.37632666e+02,
#          3.35095381e+02,  -2.95083648e+02,   2.94263473e+02,
#         -8.57731610e+01,  -1.62036228e+01,   1.30838141e+01,
#         -6.46551376e+00,   8.01826587e+00,  -3.58786095e+00,
#          1.25735987e+00,  -1.21627097e+00,   2.04033545e+00,
#         -8.04702913e-01,  -1.92666480e-01,  -1.44083371e+00,
#          1.41816098e+00,   1.70360405e+02,  -1.89070431e+01,
#          7.47139804e+00,   1.20540194e+00,   1.34588181e-01, 0.0])

# start_params.append([ -3.89054208e+00,  -2.99469508e-03,  -7.60325091e+02,
#          2.25922421e+02,   4.31682139e+01,  -2.00879587e+01,
#          3.15977299e+01,  -1.41216383e+01,   1.40729549e+01,
#         -2.29741069e-01,   5.66020784e-01,   9.50813370e-01,
#         -7.07877506e-01,  -6.33885976e-01,   2.11514130e+00,
#         -1.07084535e+00,  -1.99471358e-01,  -1.53976066e+00,
#          1.54749579e+00,   1.94668273e+02,  -1.93218649e+00,
#          4.87330211e+00,  -4.95019886e-01,   1.54561460e-01,
#          0.0])

# start_params.append([ -3.01252922e+00,   3.34774026e-03,  -3.63245948e+02,
#          7.08473344e+01,   5.18269140e+00,  -4.21852665e+01,
#          5.03986439e+01,  -3.49299323e+01,   9.39050841e+00,
#          7.10916965e+00,   2.53141800e+00,  -1.27714028e-01,
#         -8.13152443e-01,  -5.45294030e-01,   2.19662624e+00,
#         -1.03021233e+00,  -2.37376783e-01,  -1.54945600e+00,
#          1.51410989e+00,   8.93873263e+01,  -2.44415218e+01,
#          1.44237601e+01,  -2.48517486e-01,   1.57735701e-01,
#         0.0])

# start_params.append([ -2.76762846e+00,   1.89330096e-03,  -3.78969507e+02,
#          4.97375946e+01,   5.61080362e+01,  -8.13991417e+01,
#          6.18213043e+01,  -3.36881958e+01,   9.64679581e+00,
#          6.37021438e+00,   2.56205745e+00,  -6.89271288e-02,
#         -8.28256696e-01,  -5.90663693e-01,   2.19738636e+00,
#         -9.78519868e-01,  -2.34054246e-01,  -1.56404102e+00,
#          1.50934562e+00,   1.25199350e+02,  -2.58933860e+01,
#          1.60206690e+01,  -2.46344691e-01,   1.98323959e-01,
#         0.0])

# start_params.append([ -2.96336623e+00,   9.35841772e-04,  -4.69405427e+02,
#          6.56489326e+01,   6.59098372e+01,  -6.95558862e+01,
#          5.05321941e+01,  -2.68901225e+01,   6.12983979e+00,
#          8.40257564e+00,   2.03599185e+00,   1.44655457e-01,
#         -8.07626370e-01,  -6.77900254e-01,   2.19493850e+00,
#         -9.02854774e-01,  -2.35346587e-01,  -1.56947636e+00,
#          1.49891405e+00,   1.54692423e+02,  -1.84128239e+01,
#          1.40416342e+01,  -4.74336808e-01,   2.07514499e-01])

start_params.append([ -2.83157185e+00,   8.39115358e-04,  -4.21330968e+02,
         5.62354559e+01,   6.55868693e+01,  -7.39097694e+01,
         5.32753168e+01,  -2.90768080e+01,   9.73480693e+00,
         5.86938247e+00,   2.40344261e+00,   1.33807130e-01,
        -7.34188649e-01,  -8.53691403e-01,   2.20105517e+00,
        -7.61586871e-01,  -2.42532670e-01,  -1.58457873e+00,
         1.47655687e+00,   0.0, 1.48755630e+02,  0.0, -1.98109911e+01,
         1.44803287e+01,  -1.17489342e-01,   2.06651900e-01])

# start_params.append([ -3.91274686e+00,  -5.02814282e-03,  -3.60607144e+02,
#          3.08180837e+02,  -2.45731624e+02,   2.57711860e+02,
#         -7.57560376e+01,  -3.26396342e+01,   1.25979333e+01,
#         -3.17982854e+00,   7.88108320e+00,  -3.46868286e+00,
#          1.29424331e+00,  -1.31629778e+00,   2.05422384e+00,
#         -8.33747039e-01,  -1.75108086e-01,  -1.43404985e+00,
#          1.45403961e+00,   1.43868098e+02,  -2.72551797e+01,
#          8.05592823e+00,   1.03649030e+00,   1.04857599e-01,
#         -4.20237149e+01])

multi_pars = start_params
print(multi_pars)

[[-2.83157185, 0.000839115358, -421.330968, 56.2354559, 65.5868693, -73.9097694, 53.2753168, -29.076808, 9.73480693, 5.86938247, 2.40344261, 0.13380713, -0.734188649, -0.853691403, 2.20105517, -0.761586871, -0.24253267, -1.58457873, 1.47655687, 0.0, 148.75563, 0.0, -19.8109911, 14.4803287, -0.117489342, 0.2066519]]


In [18]:
def optimize_EAM_mp(pars, targets, stats, utot_func):
    
    output = fmin(sd2_loss, pars, args=(targets, stats, utot_EAM_per_atom, None, 0.05, 1), maxiter=100000, maxfun=100000, disp=0, full_output=1,ftol=1e-6)

    return tuple([output[1], output[0]])

In [19]:
params_output = []

pool = mp.Pool()

for ieam in range(1):#5, len(stats_opts[it]['hyperparams'])):

    get_sd = functools.partial(sd2_loss, targets=targets, stats=stats, utot_func=utot_EAM_per_atom, ftot_func=None, dl=0.05, verbose=1)

    get_opt = functools.partial(optimize_EAM_mp, targets=targets, stats=stats, utot_func=utot_EAM_per_atom)

    # initial ordering
    print('Initial params:', multi_pars[-1])
    
    #distances = pool.map(get_sd, multi_pars)
    
    distances = [get_sd(multi_pars[-1])]
    
    optimal_params = zip(distances, multi_pars[-1:])
    best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
    m_pars = [p[1] for p in best_params]

    print('Best params:', best_params)
    print('ieam:', ieam)
    #m_pars = multi_pars

    for i in range(50):
        #optimal_params = pool.map(get_opt, m_pars)
        optimal_params = [get_opt(m_pars)]
        best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
        m_pars = [p[1] for p in best_params]
        
        print("Iteration {}, best params: {}".format(i, best_params))

    print('Final Best params:', best_params)
    
    params_output.append(best_params)

pool.close()
pool.join()

('Initial params:', [-2.83157185, 0.000839115358, -421.330968, 56.2354559, 65.5868693, -73.9097694, 53.2753168, -29.076808, 9.73480693, 5.86938247, 2.40344261, 0.13380713, -0.734188649, -0.853691403, 2.20105517, -0.761586871, -0.24253267, -1.58457873, 1.47655687, 0.0, 148.75563, 0.0, -19.8109911, 14.4803287, -0.117489342, 0.2066519])
loss 1.02102758861e-06 1.02102758861e-06 0.0
('Best params:', [(1.0210275886100786e-06, [-2.83157185, 0.000839115358, -421.330968, 56.2354559, 65.5868693, -73.9097694, 53.2753168, -29.076808, 9.73480693, 5.86938247, 2.40344261, 0.13380713, -0.734188649, -0.853691403, 2.20105517, -0.761586871, -0.24253267, -1.58457873, 1.47655687, 0.0, 148.75563, 0.0, -19.8109911, 14.4803287, -0.117489342, 0.2066519])])
('ieam:', 0)
loss 1.02102758861e-06 1.02102758861e-06 0.0
loss 0.000797073690906 0.000797073690906 0.0
loss 1.30606525732e-06 1.30606525732e-06 0.0
loss 1.02115483151e-06 1.02115483151e-06 0.0
loss 1.03591514901e-06 1.03591514901e-06 0.0
loss 1.33158750442e-

loss 3.7096956986e-06 3.7096956986e-06 0.0
loss 1.48852557189e-06 1.48852557189e-06 0.0
loss 3.82307830562e-06 3.82307830562e-06 0.0
loss 1.46884251892e-06 1.46884251892e-06 0.0
loss 2.57209841425e-06 2.57209841425e-06 0.0
loss 2.80064675988e-06 2.80064675988e-06 0.0
loss 1.42973475815e-06 1.42973475815e-06 0.0
loss 2.91538976293e-06 2.91538976293e-06 0.0
loss 1.37302665117e-06 1.37302665117e-06 0.0
loss 2.60666930142e-06 2.60666930142e-06 0.0
loss 1.40348440455e-06 1.40348440455e-06 0.0
loss 2.75574748389e-06 2.75574748389e-06 0.0
loss 1.3544503967e-06 1.3544503967e-06 0.0
loss 2.75930492044e-06 2.75930492044e-06 0.0
loss 1.3292493053e-06 1.3292493053e-06 0.0
loss 2.33566505485e-06 2.33566505485e-06 0.0
loss 1.21739901784e-06 1.21739901784e-06 0.0
loss 2.27869639477e-06 2.27869639477e-06 0.0
loss 1.18432113172e-06 1.18432113172e-06 0.0
loss 1.84416581698e-06 1.84416581698e-06 0.0
loss 1.22035590871e-06 1.22035590871e-06 0.0
loss 1.60093786874e-06 1.60093786874e-06 0.0
loss 1.917993972

loss 1.02665009695e-06 1.02665009695e-06 0.0
loss 1.02237432257e-06 1.02237432257e-06 0.0
loss 1.02682365216e-06 1.02682365216e-06 0.0
loss 1.02214093367e-06 1.02214093367e-06 0.0
loss 1.02668962578e-06 1.02668962578e-06 0.0
loss 1.02212706078e-06 1.02212706078e-06 0.0
loss 1.02509066235e-06 1.02509066235e-06 0.0
loss 1.02619554397e-06 1.02619554397e-06 0.0
loss 1.02201073296e-06 1.02201073296e-06 0.0
loss 1.02498455518e-06 1.02498455518e-06 0.0
loss 1.02601164089e-06 1.02601164089e-06 0.0
loss 1.02198124496e-06 1.02198124496e-06 0.0
loss 1.02480346605e-06 1.02480346605e-06 0.0
loss 1.02201765564e-06 1.02201765564e-06 0.0
loss 1.02568585634e-06 1.02568585634e-06 0.0
loss 1.02193154227e-06 1.02193154227e-06 0.0
loss 1.02394329723e-06 1.02394329723e-06 0.0
loss 1.0252478702e-06 1.0252478702e-06 0.0
loss 1.02189711268e-06 1.02189711268e-06 0.0
loss 1.02527066664e-06 1.02527066664e-06 0.0
loss 1.02180887126e-06 1.02180887126e-06 0.0
loss 1.02490903611e-06 1.02490903611e-06 0.0
loss 1.02170

loss 1.02104058799e-06 1.02104058799e-06 0.0
loss 1.02104625968e-06 1.02104625968e-06 0.0
loss 1.021071549e-06 1.021071549e-06 0.0
loss 1.02103856627e-06 1.02103856627e-06 0.0
loss 1.02105024116e-06 1.02105024116e-06 0.0
loss 1.02107061619e-06 1.02107061619e-06 0.0
loss 1.02103748758e-06 1.02103748758e-06 0.0
loss 1.0210411038e-06 1.0210411038e-06 0.0
loss 1.02106930857e-06 1.02106930857e-06 0.0
loss 1.02103635604e-06 1.02103635604e-06 0.0
loss 1.02105644196e-06 1.02105644196e-06 0.0
loss 1.02105878255e-06 1.02105878255e-06 0.0
loss 1.0210371152e-06 1.0210371152e-06 0.0
loss 1.02107285152e-06 1.02107285152e-06 0.0
loss 1.02103550383e-06 1.02103550383e-06 0.0
loss 1.02105700886e-06 1.02105700886e-06 0.0
loss 1.02103715717e-06 1.02103715717e-06 0.0
loss 1.02104508662e-06 1.02104508662e-06 0.0
loss 1.02105737168e-06 1.02105737168e-06 0.0
loss 1.02103632051e-06 1.02103632051e-06 0.0
loss 1.0210410645e-06 1.0210410645e-06 0.0
loss 1.0210513294e-06 1.0210513294e-06 0.0
loss 1.02104295433e-06

loss 1.02102690716e-06 1.02102690716e-06 0.0
loss 1.02102684054e-06 1.02102684054e-06 0.0
loss 1.02102741675e-06 1.02102741675e-06 0.0
loss 1.02102678525e-06 1.02102678525e-06 0.0
loss 1.02102683744e-06 1.02102683744e-06 0.0
loss 1.02102688828e-06 1.02102688828e-06 0.0
loss 1.02102728974e-06 1.02102728974e-06 0.0
loss 1.02102676816e-06 1.02102676816e-06 0.0
loss 1.02102681279e-06 1.02102681279e-06 0.0
loss 1.02102682389e-06 1.02102682389e-06 0.0
loss 1.02102689006e-06 1.02102689006e-06 0.0
loss 1.02102679991e-06 1.02102679991e-06 0.0
loss 1.0210271896e-06 1.0210271896e-06 0.0
loss 1.02102668733e-06 1.02102668733e-06 0.0
loss 1.02102689561e-06 1.02102689561e-06 0.0
loss 1.02102706903e-06 1.02102706903e-06 0.0
loss 1.02102668622e-06 1.02102668622e-06 0.0
loss 1.02102731728e-06 1.02102731728e-06 0.0
loss 1.0210266598e-06 1.0210266598e-06 0.0
loss 1.02102675728e-06 1.02102675728e-06 0.0
loss 1.02102680169e-06 1.02102680169e-06 0.0
loss 1.02102727886e-06 1.02102727886e-06 0.0
loss 1.0210266

...

loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.00465131722e-06 1.00465131722e-06 0.0
loss 1.00465131788e-06 1.00465131788e-06 0.0
loss 1.00465131611e-06 1.00465131611e-06 0.0
loss 1.00465131655e-06 1.00465131655e-06 0.0
loss 1.00465131811e-06 1.00465131811e-06 0.0
loss 1.00465131589e-06 1.00465131589e-06 0.0
loss 1.00465131766e-06 1.00465131766e-06 0.0
loss 1.004651317e-06 1.004651317e-06 0.0
loss 1.00465131655e-06 1.00465131655e-06 0.0
loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.004651317e-06 1.004651317e-06 0.0
loss 1.00465131811e-06 1.00465131811e-06 0.0
loss 1.00465131811e-06 1.00465131811e-06 0.0
loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.00465131722e-06 1.00465131722e-06 0.0
loss 1.00465131811e-06 1.00465131811e-06 0.0
loss 1.00465131633e-06 1.00465131633e-06 0.0
loss 1.00465131811e-06 1.00465131811e-06 0.0
loss 1.00465131633e-06 1.00465131633e-06 0.0
loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.00465131655e-06 1.00465131655e-06 0.0
loss 1.00465131655

loss 1.00465131855e-06 1.00465131855e-06 0.0
loss 1.004651317e-06 1.004651317e-06 0.0
loss 1.004651315e-06 1.004651315e-06 0.0
loss 1.004651317e-06 1.004651317e-06 0.0
loss 1.00465131966e-06 1.00465131966e-06 0.0
loss 1.00465131566e-06 1.00465131566e-06 0.0
loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.004651317e-06 1.004651317e-06 0.0
loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.00465131833e-06 1.00465131833e-06 0.0
loss 1.00465131589e-06 1.00465131589e-06 0.0
loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.00465131677e-06 1.00465131677e-06 0.0
loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.00465131633e-06 1.00465131633e-06 0.0
loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.00465131633e-06 1.00465131633e-06 0.0
loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.00465131877e-06 1.00465131877e-06 0.0
loss 1.00465131722e-06 1.00465131722e-06 0.0
loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.004651317e-06 1.004

loss 1.00465131655e-06 1.00465131655e-06 0.0
loss 1.00465131677e-06 1.00465131677e-06 0.0
loss 1.00465131744e-06 1.00465131744e-06 0.0
loss 1.00465131766e-06 1.00465131766e-06 0.0
loss 1.00465131722e-06 1.00465131722e-06 0.0
loss 1.00465131677e-06 1.00465131677e-06 0.0
loss 1.00465131655e-06 1.00465131655e-06 0.0
loss 1.004651317e-06 1.004651317e-06 0.0
loss 1.00465131788e-06 1.00465131788e-06 0.0
loss 1.00465131766e-06 1.00465131766e-06 0.0
loss 1.00465131722e-06 1.00465131722e-06 0.0
loss 1.00465131766e-06 1.00465131766e-06 0.0
loss 1.00465131833e-06 1.00465131833e-06 0.0
loss 1.00465131589e-06 1.00465131589e-06 0.0
loss 1.00465131833e-06 1.00465131833e-06 0.0
loss 1.00465131633e-06 1.00465131633e-06 0.0
loss 1.004651315e-06 1.004651315e-06 0.0
loss 1.004651317e-06 1.004651317e-06 0.0
loss 1.00465131855e-06 1.00465131855e-06 0.0
loss 1.00465131722e-06 1.00465131722e-06 0.0
loss 1.00465131722e-06 1.00465131722e-06 0.0
loss 1.00465131855e-06 1.00465131855e-06 0.0
loss 1.00465131655e-06

Process PoolWorker-3:
Process PoolWorker-1:
  File "//anaconda/lib/python2.7/multiprocessing/process.py", line 258, in _bootstrap
Process PoolWorker-4:
Process PoolWorker-2:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "//anaconda/lib/python2.7/multiprocessing/process.py", line 258, in _bootstrap
  File "//anaconda/lib/python2.7/multiprocessing/process.py", line 258, in _bootstrap
  File "//anaconda/lib/python2.7/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
    self.run()
    self.run()
  File "//anaconda/lib/python2.7/multiprocessing/process.py", line 114, in run
    self.run()
  File "//anaconda/lib/python2.7/multiprocessing/process.py", line 114, in run
  File "//anaconda/lib/python2.7/multiprocessing/process.py", line 114, in run
    self._target(*self._args, **self._kwargs)
    self._target(*self._args, **self._kwargs)
    self._target(*self._args, **self._k

KeyboardInterrupt: 

In [ ]:
params_output = [(8.9710060363567114e-07, np.array([ -4.18353755e+00,  -9.63668936e-03,  -1.00171035e+02,
         1.90025394e+01,   2.15938317e+01,  -1.39759833e+01,
         2.16332289e+01,  -3.29542126e+00,   1.70455674e+00,
         1.41347064e+00,  -9.02958785e-01,  -8.62309098e-01,
         1.95964588e+00,  -8.70527088e-01,   3.22342700e-02,
        -1.53866121e+00,   1.37095441e+00,  -4.32896107e+01,
         4.64461212e+00,   3.23329113e-01,   5.82061842e-02]))]

In [ ]:
params_output = [(8.829397265807305e-07, np.array([ -4.33954858e+00,  -1.02215197e-02,  -1.12590032e+02,
         3.06702045e+01,   1.74951979e+01,  -1.33298120e+01,
         2.13899957e+01,  -3.70881631e+00,   1.56452640e+00,
         1.27789071e+00,  -8.54623702e-01,  -8.39818015e-01,
         1.95990543e+00,  -8.75948596e-01,   1.81927625e-02,
        -1.54683863e+00,   1.38614460e+00,  -4.28747460e+01,
         4.18974818e+00,   1.56622590e-01,   5.72961538e-02,
         3.46319317e+00]))]

In [ ]:
params_output = [(8.7421414571196454e-07, np.array([ -4.31249172e+00,  -9.93971047e-03,  -3.76018390e+01,
        -1.14759006e+02,   1.72557600e+01,   2.66437414e+01,
        -1.50817090e+01,   2.22342349e+01,  -3.62963119e+00,
         1.62230813e+00,   1.18480877e+00,  -8.52354746e-01,
        -8.38460594e-01,   1.98957701e+00,  -8.86622667e-01,
         1.66082225e-03,  -1.54824194e+00,   1.39761513e+00,
        -5.06767503e+01,   4.47029066e+00,   9.10205250e-02,
         5.87302830e-02,   1.82639066e+00]))]

In [ ]:
params_output = [(8.8257346852300666e-07, np.array([ -4.36548916e+00,  -1.11867827e-02,  -1.94093020e+01,
        -1.40195282e+02,   4.53864231e+01,   1.49756180e+01,
        -1.36031385e+01,   2.21581200e+01,  -4.61501041e+00,
         2.06360250e+00,   1.12795645e+00,  -8.01200744e-01,
        -8.58426028e-01,   1.95860157e+00,  -8.68817546e-01,
         2.43936831e-02,  -1.54555297e+00,   1.38005891e+00,
        -5.22754243e+01,   3.98209114e+00,   3.07369702e-01,
         5.51658454e-02,   1.58601447e+00]))]

In [ ]:
params_output = [(2.8925274000958436e-06, np.array([ -3.09187534e+00,   1.19622206e-04,  -5.67875917e+02,
         3.21802084e+02,  -4.71317094e+02,   3.98296604e+02,
        -1.13270858e+02,   6.03114401e+00,   1.48067908e+01,
        -1.57531660e+01,   7.80863462e+00,  -2.99246651e+00,
         7.33596451e-01,  -9.50794219e-01,   1.94186078e+00,
        -8.83596676e-01,  -1.33608784e-01,  -1.46694544e+00,
         1.42447434e+00,   7.53865380e+01,   3.29733034e-01,
         2.18327852e+00,   6.63152141e-02]))]

In [ ]:
# convert lists of optimal parameters to dictionaries
params_optimal = []
for pars in params_output:
    #params_optimal.append(to_param_dict(pars, [2, 15, 4, 0]))
    params_optimal.append(to_param_dict(pars[1], stats['hyperparams']))

In [ ]:
# store hyperparameters and output parameters in a single file
try:
    with open(os.path.join(working, 'params_store'+'.pickle'), 'rb') as fi:
        params_store = pickle.load(fi)    
except IOError:
    print('no file')
    params_store = []
    
params_store.extend(params_optimal)

with open(os.path.join(working, "params_store.pickle"), 'wb') as fo:
    pickle.dump(params_store, fo, protocol=2)

In [ ]:
with open(os.path.join(working, 'params_store' + '.pickle'), 'rb') as fi:
    retreived_params = pickle.load(fi)  

In [ ]:
retreived_params